
# KL-SVD on Burgers equation

Example using KL-SVD on solutions of the Burgers equation.


In [ ]:
from __future__ import annotations

import matplotlib.pyplot as plt
from gemseo import configure_logger
from gemseo.mlearning.transformers.dimension_reduction.klsvd import KLSVD
from gemseo.problems.dataset.burgers import create_burgers_dataset

configure_logger()

## Load dataset



In [ ]:
dataset = create_burgers_dataset(n_samples=20)
print(dataset)

t = dataset.input_dataset.to_numpy()[:, 0]
u_t = dataset.output_dataset.to_numpy()
t_split = 0.87

## Plot dataset



In [ ]:
def lines_gen():
    """Linestyle generator."""
    yield "-"
    for i in range(1, dataset.n_samples):
        yield 0, (i, 1, 1, 1)


color = "red"
lines = lines_gen()
for i in range(dataset.n_samples):
    # Switch mode if discontinuity is gone
    if color == "red" and t[i] > t_split:
        color = "blue"
        lines = lines_gen()  # reset linestyle generator

    plt.plot(u_t[i], color=color, linestyle=next(lines), label=f"t={t[i]:.2f}")

plt.legend()
plt.title("Solutions to Burgers equation")
plt.show()

## Create KLSVD



In [ ]:
n_modes = 7
klsvd = KLSVD(dataset.misc["x"], n_modes)
klsvd.fit(u_t)
u_t_reduced = klsvd.transform(u_t)
u_t_restored = klsvd.inverse_transform(u_t_reduced)

print(f"Dimension of the reduced space: {klsvd.output_dimension}")

## Plot restored data



In [ ]:
color = "red"
lines = lines_gen()
for i in range(dataset.n_samples):
    # Switch mode if discontinuity is gone
    if color == "red" and t[i] > t_split:
        color = "blue"
        lines = lines_gen()  # reset linestyle generator

    plt.plot(
        u_t_restored[i],
        color=color,  # linestyle=next(lines),
        label=f"t={t[i]:.2f}",
    )

plt.legend()
plt.title("Reconstructed solution after KLSVD reduction.")
plt.show()